In [1]:
# modified from https://github.com/SherlockLiao/Deep-Dream/blob/master/show_image.ipynb
import torch
import torchvision.models as models
from torchvision import transforms
from PIL import Image
from deepDream import dream
import torch.nn as nn
import spectroUtils as sUtils
import IPython.display as ipd
import librosa
import librosa.display
import numpy as np

('track', 'tags')
('album', 'tags')
('artist', 'tags')
('track', 'genres')
('track', 'genres_all')


/home/iaakhter/cs532l/DreamingInMusic/utils.py:218: FutureWarning: specifying 'categories' or 'ordered' in .astype() is deprecated; pass a CategoricalDtype instead
  'category', categories=SUBSETS, ordered=True)


In [2]:
#Original hip-hopaudio
trackId = 2
spectroSize = 224
minAmp = -80.0
maxAmp = 1.9073486e-06
audioDirectory = "data/fma_small/"
audioFilename = audioDirectory + "000/000002.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)
start, end = 0, 30
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [3]:
scaledSpectro, phase, origSpectroSize = sUtils.loadSpectro(trackId, spectroSize, minAmp, maxAmp)
scaledSpectro = scaledSpectro.data.numpy()
#scaledSpectro = scaledSpectro/255.0
scaledSpectro

array([[[130., 171., 179., ..., 210., 175., 180.],
        [172., 186., 190., ..., 208., 196., 186.],
        [194., 199., 198., ..., 209., 208., 213.],
        ...,
        [ 53.,  51.,  63., ...,  66.,  45., 106.],
        [ 41.,  46.,  71., ...,  65.,  59., 106.],
        [ 53.,  62.,  68., ...,  63.,  56., 107.]]])

In [4]:
model = models.__dict__['resnet18']()
model = torch.nn.DataParallel(model)
model

DataParallel (
  (module): ResNet (
    (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
    (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
    (relu): ReLU (inplace)
    (maxpool): MaxPool2d (size=(3, 3), stride=(2, 2), padding=(1, 1), dilation=(1, 1))
    (layer1): Sequential (
      (0): BasicBlock (
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
        (relu): ReLU (inplace)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn2): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
      )
      (1): BasicBlock (
        (conv1): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
        (bn1): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
        (relu): ReLU (inplace)
        (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride

In [5]:
checkpoint_path = 'resnet18/checkpoints/model_best.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
model.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))

=> loading checkpoint 'resnet18/checkpoints/model_best.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/model_best.pth.tar' (epoch: 57) (best_acc: 50.57766367627047)


In [6]:
model = nn.Sequential(*list(model.children())[:-3])
model

Sequential (
)

In [7]:
dreamSpectro = dream(model, scaledSpectro)
dreamSpectro = dreamSpectro[0,:]
print ("dreamSpectro")
print (dreamSpectro)

(1, 41, 41)
ratio 138.42328
learning_rate_use 0.0036121092081006136
imgBefore [[[130.46957  184.39403  218.82312  ... 208.74127  201.26163  180.65018 ]
  [161.15906  189.93245  202.84962  ... 194.9291   200.75099  192.99127 ]
  [160.79375  186.64621  196.95079  ... 193.15549  197.81546  192.57227 ]
  ...
  [ 51.72398   59.917404  59.238594 ...  60.318638  59.707806 106.67886 ]
  [ 52.731373  58.83989   58.51147  ...  58.73556   59.396572 106.51072 ]
  [ 53.19144   62.065086  60.005222 ...  62.132355  59.94361  107.3865  ]]]
imgAfter (1, 41, 41)
ratio 138.92328
learning_rate_use 0.0035991088339405804
imgBefore [[[130.93915  185.05768  219.61069  ... 209.49255  201.986    181.30035 ]
  [161.73909  190.61604  203.5797   ... 195.63066  201.47351  193.68587 ]
  [161.37247  187.31796  197.65964  ... 193.85068  198.52742  193.26535 ]
  ...
  [ 51.91014   60.133053  59.4518   ...  60.535732  59.9227   107.06281 ]
  [ 52.921158  59.051662  58.72206  ...  58.946957  59.610348 106.894066]
  [ 53.

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


ratio 153.21027
learning_rate_use 0.0032634888815499343
imgBefore [[[144.07822  198.04256  210.59747  ... 230.98514  215.50935  199.4928  ]
  [177.11494  207.97227  213.60983  ... 220.48253  221.66533  215.61497 ]
  [178.19154  207.25842  209.33194  ... 222.44507  221.57495  209.364   ]
  ...
  [ 59.51586   65.39927   65.1434   ...  65.45629   65.26697  117.517784]
  [ 57.269997  65.42732   63.649742 ...  64.924736  68.25369  117.71931 ]
  [ 58.739517  67.72387   69.31303  ...  67.24084   66.52513  118.58745 ]]]
imgAfter (1, 58, 58)
ratio 153.71028
learning_rate_use 0.0032528728432270745
imgBefore [[[144.54689  198.68677  211.28252  ... 231.7365   216.21037  200.14172 ]
  [177.69107  208.64879  214.30467  ... 221.19974  222.38638  216.31635 ]
  [178.77118  207.9326   210.01286  ... 223.16866  222.2957   210.04503 ]
  ...
  [ 59.709457  65.61201   65.35531  ...  65.66921   65.47927  117.900055]
  [ 57.456287  65.64015   63.856785 ...  65.135925  68.475716 118.102234]
  [ 58.930588  67.9

imgBefore [[[159.53139  212.37918  223.30997  ... 240.00519  233.06859  220.88943 ]
  [214.53017  223.93936  232.7073   ... 245.17389  245.20033  240.18309 ]
  [196.20776  215.05537  233.47824  ... 242.53006  255.74973  254.48775 ]
  ...
  [ 65.24552   74.538216  65.62966  ...  70.425644  86.2138   130.80296 ]
  [ 61.25975   73.44829   71.36425  ...  78.76487   81.12369  130.21024 ]
  [ 65.03964   75.628555  71.66097  ...  76.48809   79.204704 131.30656 ]]]
imgAfter (1, 114, 114)
ratio 170.55917
learning_rate_use 0.0029315339040019268
imgBefore [[[159.99905  213.00177  223.96461  ... 240.70877  233.75183  221.53699 ]
  [215.15907  224.59584  233.3895   ... 245.89262  245.91914  240.88719 ]
  [196.78296  215.68582  234.16269  ... 243.24104  255.74754  255.23378 ]
  ...
  [ 65.43679   74.75673   65.82206  ...  70.632095  86.46654  131.18642 ]
  [ 61.439335  73.663605  71.573456 ...  78.99577   81.3615   130.59195 ]
  [ 65.23031   75.850266  71.87105  ...  76.71232   79.4369   131.6915  ]

ratio 183.64195
learning_rate_use 0.0027226894135756745
imgBefore [[[172.63617  224.56114  235.58354  ... 254.95013  250.15662  239.03455 ]
  [230.26094  245.87048  255.69429  ... 255.69429  255.69429  255.69429 ]
  [231.97127  221.20694  239.90584  ... 255.69429  249.43007  255.69429 ]
  ...
  [ 71.75026   79.35138   82.39928  ...  87.28463   89.93409  140.89645 ]
  [ 62.719017  74.312416  84.46845  ...  92.26146   85.829575 140.95143 ]
  [ 70.38233   83.26168   79.26235  ...  86.83197   86.40713  142.09279 ]]]
imgAfter (1, 160, 160)
ratio 184.10516
learning_rate_use 0.002715839090512167
imgBefore [[[173.10503  225.17102  236.22334  ... 255.64253  250.836    239.68373 ]
  [230.88629  246.53822  255.69254  ... 255.69254  255.69254  255.69254 ]
  [232.60126  221.80771  240.55739  ... 255.69254  250.10748  255.69254 ]
  ...
  [ 71.94512   79.56689   82.62306  ...  87.52168   90.17834  141.2791  ]
  [ 62.88935   74.51424   84.69785  ...  92.512024  86.062675 141.33423 ]
  [ 70.57348   83.

In [8]:
#Convert it back to 
backToSpectro = sUtils.unscaleSpectro(dreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)

## Control The Dream

In [23]:
otherTrackId = 6366
otherSpectro, otherPhase, otherOrigSpectroSize = sUtils.loadSpectro(otherTrackId, spectroSize, minAmp, maxAmp)
otherSpectro = otherSpectro.data.numpy()
audioFilename = audioDirectory + "006/006366.mp3"
x, sr = librosa.load(audioFilename, sr=None, mono=True, duration = 10, offset = 0)
start, end = 0, 10
ipd.Audio(data=x[start*sr:end*sr], rate=sr)

In [14]:
model = models.__dict__['resnet18']()
model = torch.nn.DataParallel(model)
checkpoint_path = 'resnet18/checkpoints/model_best.pth.tar'
print("=> loading checkpoint '{}'".format(checkpoint_path))
checkpoint = torch.load(checkpoint_path)
start_epoch = checkpoint['epoch']
best_prec1 = checkpoint['best_prec1']
model.load_state_dict(checkpoint['state_dict'])
print("=> loaded checkpoint '{}' (epoch: {}) (best_acc: {})"
        .format(checkpoint_path, checkpoint['epoch'], checkpoint['best_prec1']))
model = nn.Sequential(*list(model.children())[:-3])

=> loading checkpoint 'resnet18/checkpoints/model_best.pth.tar'
=> loaded checkpoint 'resnet18/checkpoints/model_best.pth.tar' (epoch: 57) (best_acc: 50.57766367627047)


In [15]:
control_features = model.forward(otherSpectro)

In [16]:
def objective_guide(dst, guide_features):
    x = dst.data[0].cpu().numpy().copy()
    #print ("guide_features", guide_features.shape)
    y = guide_features
    w, h = x.shape
    ch = 1
    x = x.reshape(ch,-1)
    y = y.reshape(ch,-1)
    A = x.T.dot(y) # compute the matrix of dot-products with guide features
    result = y[:,A.argmax(1)] # select ones that match best
    if torch.cuda.is_available():
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float)).cuda()
    else:
        result = torch.Tensor(np.array([result.reshape(ch, w, h)], dtype=np.float))
    return result

In [20]:
hopRockDreamSpectro = dream(model, scaledSpectro, control=control_features, distance=objective_guide)
print(hopRockDreamSpectro)

/home/iaakhter/.conda/envs/mypy35/lib/python3.5/site-packages/scipy/ndimage/interpolation.py:616: UserWarning: From scipy 0.13.0, the output shape of zoom() is calculated with round() instead of int() - for these inputs the size of the returned array has changed.
  "the returned array has changed.", UserWarning)


(1, 41, 41)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[130.5      184.23038  218.53555  ... 208.48999  201.03726  180.5     ]
  [161.07903  189.74886  202.61955  ... 194.72752  200.52847  192.79668 ]
  [160.71503  186.47446  196.74194  ... 192.9603   197.6035   192.37918 ]
  ...
  [ 52.03782   60.201756  59.525387 ...  60.601543  59.992912 106.794914]
  [ 53.041588  59.128117  58.80088  ...  59.024166  59.682796 106.62737 ]
  [ 53.5       62.34171   60.289257 ...  62.408733  60.227867 107.5     ]]]
imgAfter (1, 41, 41)


/home/iaakhter/cs532l/DreamingInMusic/deepDream.py:47: UserWarning: other is not broadcastable to self, but they have the same number of elements.  Falling back to deprecated pointwise behavior.
  img_variable.data.add_(img_variable.grad.data * learning_rate_use)


ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[131.       184.73038  219.03555  ... 208.98999  201.53726  181.      ]
  [161.57903  190.24886  203.11955  ... 195.22752  201.02847  193.29668 ]
  [161.21503  186.97446  197.24194  ... 193.4603   198.1035   192.87918 ]
  ...
  [ 52.53782   60.701756  60.025387 ...  61.101543  60.492912 107.294914]
  [ 53.541588  59.628117  59.30088  ...  59.524166  60.182796 107.12737 ]
  [ 54.        62.84171   60.789257 ...  62.908733  60.727867 108.      ]]]
imgAfter (1, 41, 41)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[131.5      185.23038  219.53555  ... 209.48999  202.03726  181.5     ]
  [162.07903  190.74886  203.61955  ... 195.72752  201.52847  193.79668 ]
  [161.71503  187.47446  197.74194  ... 193.9603   198.6035   193.37918 ]
  ...
  [ 53.03782   61.201756  60.525387 ...  61.601543  60.992912 107.794914]
  [ 54.041588  60.128117  59.80088  ...  60.024166  60.682796 107.62737 ]
  [ 54.5       63.34171   61.28

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[139.       192.73038  227.03555  ... 216.98999  209.53726  189.      ]
  [169.57903  198.24886  211.11955  ... 203.22752  209.02847  201.29668 ]
  [169.21503  194.97446  205.24194  ... 201.4603   206.1035   200.87918 ]
  ...
  [ 60.53782   68.70175   68.02539  ...  69.10155   68.49291  115.294914]
  [ 61.541588  67.62811   67.30088  ...  67.52417   68.1828   115.12737 ]
  [ 62.        70.841705  68.78926  ...  70.90874   68.72787  116.      ]]]
imgAfter (1, 41, 41)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[139.5      193.23038  227.53555  ... 217.48999  210.03726  189.5     ]
  [170.07903  198.74886  211.61955  ... 203.72752  209.52847  201.79668 ]
  [169.71503  195.47446  205.74194  ... 201.9603   206.6035   201.37918 ]
  ...
  [ 61.03782   69.20175   68.52539  ...  69.60155   68.99291  115.794914]
  [ 62.041588  68.12811   67.80088  ...  68.02417   68.6828   115.62737 ]
  [ 62.5       71.341705  69.28

...

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[155.       204.79515  204.02675  ... 222.1146   217.65483  205.      ]
  [197.55887  211.25935  216.46439  ... 218.92944  228.63417  227.86674 ]
  [167.45554  213.99704  212.86794  ... 221.62234  228.98972  208.30725 ]
  ...
  [ 77.42769   85.86941   83.83367  ...  80.84008   87.13038  131.11292 ]
  [ 76.04263   83.89457   82.993965 ...  85.01598   87.51078  131.26614 ]
  [ 78.        85.73632   86.994    ...  81.54579   85.70667  132.      ]]]
imgAfter (1, 81, 81)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[155.5      205.29515  204.52675  ... 222.6146   218.15483  205.5     ]
  [198.05887  211.75935  216.96439  ... 219.42944  229.13417  228.36674 ]
  [167.95554  214.49704  213.36794  ... 222.12234  229.48972  208.80725 ]
  ...
  [ 77.92769   86.36941   84.33367  ...  81.34008   87.63038  131.61292 ]
  [ 76.54263   84.39457   83.493965 ...  85.51598   88.01078  131.76614 ]
  [ 78.5       86.23632   87.49

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[163.       209.82135  217.03056  ... 228.87877  223.39122  213.      ]
  [213.63516  219.18617  225.1514   ... 233.51796  234.17427  230.20844 ]
  [194.05626  209.29704  225.20483  ... 230.60889  247.4844   243.92554 ]
  ...
  [ 86.37602   94.75408   85.49193  ...  87.88768  100.43896  139.64519 ]
  [ 82.4043    93.624565  91.06658  ...  96.12117   95.380066 139.      ]
  [ 86.        95.59731   91.08582  ...  93.97228   93.52018  140.      ]]]
imgAfter (1, 114, 114)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[163.5      210.32135  217.53056  ... 229.37877  223.89122  213.5     ]
  [214.13516  219.68617  225.6514   ... 234.01796  234.67427  230.70844 ]
  [194.55626  209.79704  225.70483  ... 231.10889  247.9844   244.42554 ]
  ...
  [ 86.87602   95.25408   85.99193  ...  88.38768  100.93896  140.14519 ]
  [ 82.9043    94.124565  91.56658  ...  96.62117   95.880066 139.5     ]
  [ 86.5       96.09731   91.

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[171.       215.22014  221.61008  ... 233.2893   230.08806  221.      ]
  [221.85535  233.03267  240.86797  ... 241.8737   244.87817  237.86792 ]
  [221.31445  207.7304   223.19302  ... 248.56715  234.14742  238.7044  ]
  ...
  [ 95.61006  101.92366  104.374664 ... 104.270996 103.09047  147.      ]
  [ 86.83019   96.96922  106.21795  ... 109.13152   99.21016  147.      ]
  [ 94.       105.41509  100.949684 ... 104.        99.81761  148.      ]]]
imgAfter (1, 160, 160)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[171.5      215.72014  222.11008  ... 233.7893   230.58806  221.5     ]
  [222.35535  233.53267  241.36797  ... 242.3737   245.37817  238.36792 ]
  [221.81445  208.2304   223.69302  ... 249.06715  234.64742  239.2044  ]
  ...
  [ 96.11006  102.42366  104.874664 ... 104.770996 103.59047  147.5     ]
  [ 87.33019   97.46922  106.71795  ... 109.63152   99.71016  147.5     ]
  [ 94.5      105.91509  101.

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[179.       223.22014  229.61008  ... 241.2893   238.08806  229.      ]
  [229.85535  241.03267  248.86797  ... 249.8737   252.87817  245.86792 ]
  [229.31445  215.7304   231.19302  ... 255.5      242.14742  246.7044  ]
  ...
  [103.61006  109.92366  112.374664 ... 112.270996 111.09047  155.      ]
  [ 94.83019  104.96922  114.21795  ... 117.13152  107.21016  155.      ]
  [102.       113.41509  108.949684 ... 112.       107.81761  156.      ]]]
imgAfter (1, 160, 160)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[179.5      223.72014  230.11008  ... 241.7893   238.58806  229.5     ]
  [230.35535  241.53267  249.36797  ... 250.3737   253.37817  246.36792 ]
  [229.81445  216.2304   231.69302  ... 255.5      242.64742  247.2044  ]
  ...
  [104.11006  110.42366  112.874664 ... 112.770996 111.59047  155.5     ]
  [ 95.33019  105.46922  114.71795  ... 117.63152  107.71016  155.5     ]
  [102.5      113.91509  109.

ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[187.5     228.50002 236.50002 ... 255.5     232.5     237.5    ]
  [229.5     243.5     247.5     ... 255.5     253.5     243.5    ]
  [251.5     255.5     255.5     ... 255.5     255.5     255.5    ]
  ...
  [110.5     108.5     120.5     ... 123.5     102.5     163.5    ]
  [ 98.5     103.5     128.5     ... 122.5     116.5     163.5    ]
  [110.5     119.5     125.5     ... 120.5     113.5     164.5    ]]]
imgAfter (1, 224, 224)
ratio 255.0
learning_rate_use 0.00196078431372549
imgBefore [[[188.      229.00002 237.00002 ... 255.5     233.      238.     ]
  [230.      244.      248.      ... 255.5     254.      244.     ]
  [252.      255.5     255.5     ... 255.5     255.5     255.5    ]
  ...
  [111.      109.      121.      ... 124.      103.      164.     ]
  [ 99.      104.      129.      ... 123.      117.      164.     ]
  [111.      120.      126.      ... 121.      114.      165.     ]]]
imgAfter (1, 224, 224)
ra

In [21]:
hopRockDreamSpectro = hopRockDreamSpectro[0,:]
#Convert it back to 
backToSpectro = sUtils.unscaleSpectro(hopRockDreamSpectro, origSpectroSize, minAmp, maxAmp)
# Multiply power spectrogram with phase to get original complex spectrogram
backToSpectro = backToSpectro*phase

# Revert complex spectrogram to audio
n = len(x)
y_hat = librosa.istft(backToSpectro, length = n)
ipd.Audio(data=y_hat[start*sr:end*sr], rate=sr)